In [1]:
%load_ext autoreload
%autoreload 2

In [85]:
from collections import Counter, defaultdict
from glob import glob
import json
from socket import inet_pton, AF_INET, AF_INET6
from subprocess import Popen
from traceutils.radix.ip2as import create_private, create_table
from traceutils.utils.net import inet_fix, prefix_addrs
import re
import finder as vf
import bz2
from collections import Counter, defaultdict, namedtuple
from lxml import etree

In [86]:
Info = namedtuple('Info', ['addr', 'router', 'pdesc', 'ldesc'])
def parse_xml(filename):
    nodes = defaultdict(set)
    addrs = {}
    parser = etree.XMLParser(ns_clean=True, recover=True)
    root = etree.parse(filename, parser)
    routers = root.findall('.//{*}router')
    for router in routers:
        rname = router.attrib['name']
        iface_info = router.find('{*}interface-information')
        for physical in iface_info.findall('.//{*}physical-interface'):
            pdesc = physical.find('.//{*}description')
            pdesc = pdesc.text if pdesc is not None else None
            for logical in physical.findall('.//{*}logical-interface'):
                ldesc = logical.find('.//{*}description')
                ldesc = ldesc.text if ldesc is not None else None
                for family in logical.findall('.//{*}address-family'):
                    name = family.find('.//{*}address-family-name')
                    if name is not None and name.text == 'inet':
                        for local in family.findall('.//{*}ifa-local'):
                            addr = local.text
                            info = Info(addr, rname, pdesc, ldesc)
                            nodes[rname].add(addr)
                            addrs[addr] = rname
    return nodes, addrs

In [87]:
routers, addrs = parse_xml('../verify_bdrmapit/verify_bdrmapit/i2/show_interfaces.20180313.xml')

In [3]:
ip2as = create_table('../ip2as/test.csv')

In [4]:
files = []
for file in glob('../retrieve-external/team/*.warts*'):
    monitor = re.search(r'\.([-a-z0-9]+)\.warts', file).group(1)
    wf = vf.WartsFile(file, monitor)
    files.append(wf)
len(files)

236

In [75]:
[(i, f.filename) for i, f in enumerate(files)]

[(0,
  '../retrieve-external/team/daily.l7.t3.c006865.20180801.iad3-us.warts.gz'),
 (1,
  '../retrieve-external/team/daily.l7.t1.c006867.20180802.tul3-us.warts.gz'),
 (2,
  '../retrieve-external/team/daily.l7.t2.c006866.20180802.oua2-bf.warts.gz'),
 (3, '../retrieve-external/team/daily.l7.t2.c006866.20180802.ams-nl.warts.gz'),
 (4, '../retrieve-external/team/daily.l7.t2.c006866.20180802.dar-tz.warts.gz'),
 (5,
  '../retrieve-external/team/daily.l7.t2.c006866.20180801.sjc2-us.warts.gz'),
 (6, '../retrieve-external/team/daily.l7.t1.c006867.20180802.syd-au.warts.gz'),
 (7,
  '../retrieve-external/team/daily.l7.t1.c006867.20180801.osl2-no.warts.gz'),
 (8,
  '../retrieve-external/team/daily.l7.t2.c006866.20180802.psa2-it.warts.gz'),
 (9,
  '../retrieve-external/team/daily.l7.t3.c006865.20180802.hkg3-cn.warts.gz'),
 (10,
  '../retrieve-external/team/daily.l7.t1.c006867.20180802.hkg-cn.warts.gz'),
 (11,
  '../retrieve-external/team/daily.l7.t2.c006866.20180801.iad-us.warts.gz'),
 (12,
  '../r

In [88]:
addrs['162.252.70.60']

'ashb'

In [89]:
addrs['162.252.70.136']

'wash'

In [90]:
addrs['62.40.124.45']

'wash'

In [84]:
test, bins = vf.mplstest(files[12].filename, ip2as)
len(bins)

01: 128.9.112.7 False
02: 198.32.16.30 False
03: 137.164.27.241 False
04: 137.164.26.201 False
05: 162.252.70.115 True
06: 162.252.70.144 True
07: 162.252.70.140 True
08: 162.252.70.60 True
09: 162.252.70.136 False
10: 62.40.124.44 False
11: 62.40.98.79 False
12: 62.40.98.77 False
13: 62.40.98.153 False

01: 128.9.112.7 False
02: 198.32.16.30 False
03: 137.164.27.241 False
04: 137.164.26.201 False
05: 162.252.70.115 True
06: 162.252.70.144 True
07: 162.252.70.140 False
08: 141.225.250.25 False
09: 141.225.249.17 False
10: 141.225.249.6 False

01: 128.9.112.7 False
02: 198.32.16.30 False
03: 137.164.27.241 False
04: 137.164.26.201 False
05: 162.252.70.115 True
06: 162.252.70.144 True
07: 162.252.70.140 True
08: 162.252.70.60 True
09: 162.252.70.136 False
10: 62.40.124.44 False
11: 62.40.124.198 False
12: 146.97.33.2 False
13: 146.97.33.22 False
14: 146.97.33.42 False
15: 146.97.33.54 False
16: 146.97.38.38 False
17: 146.97.74.34 False
18: 146.97.156.78 False
19: 194.81.57.209 False
20: 

01: 128.9.112.7 False
02: 198.32.16.30 False
03: 137.164.27.241 False
04: 137.164.26.201 False
05: 162.252.70.115 True
06: 162.252.70.144 True
07: 162.252.70.140 True
08: 162.252.70.60 True
09: 162.252.70.136 False
10: 62.40.124.44 False
11: 62.40.124.198 False
12: 146.97.33.2 False
13: 146.97.37.194 False
14: 193.63.108.94 False
15: 193.63.108.98 False
16: 193.63.109.90 False

01: 128.9.112.7 False
02: 198.32.16.30 False
03: 137.164.23.225 False
04: 137.164.11.35 False
05: 64.57.20.82 False
06: 162.252.70.115 True
07: 162.252.70.144 True
08: 162.252.70.140 True
09: 162.252.70.133 True
10: 162.252.70.130 True
11: 206.126.236.45 False
12: 206.126.236.140 False
13: 166.49.208.76 False
14: 213.137.183.35 False
15: 109.159.252.137 False
16: 213.121.192.3 False

01: 128.9.112.7 False
02: 198.32.16.30 False
03: 137.164.27.241 False
04: 137.164.26.201 False
05: 162.252.70.115 True
06: 162.252.70.144 True
07: 162.252.70.140 True
08: 162.252.70.60 True
09: 162.252.70.136 True
10: 162.252.70.139

01: 128.9.112.7 False
02: 198.32.16.30 False
03: 137.164.27.241 False
04: 137.164.26.201 False
05: 162.252.70.115 True
06: 162.252.70.144 True
07: 162.252.70.140 True
08: 162.252.70.60 True
09: 162.252.70.136 False
10: 62.40.124.44 False
11: 62.40.124.198 False
12: 146.97.33.2 False
13: 146.97.37.250 False
14: 146.97.68.45 False
15: 146.97.146.166 False

01: 128.9.112.7 False
02: 198.32.16.30 False
03: 137.164.23.225 False
04: 137.164.11.7 False
05: 64.57.20.82 False
06: 162.252.70.115 True
07: 162.252.70.144 True
08: 162.252.70.140 True
09: 162.252.70.133 True
10: 162.252.70.130 True
11: 206.126.236.45 False
12: 206.126.236.140 False
13: 166.49.195.77 False
14: 213.137.183.33 False
15: 109.159.249.22 False
16: 109.159.249.79 False
17: 213.120.176.186 False
18: 217.41.219.195 False

01: 128.9.112.7 False
02: 198.32.16.30 False
03: 137.164.23.225 False
04: 137.164.11.27 False
05: 64.57.20.82 False
06: 162.252.70.115 True
07: 162.252.70.144 True
08: 162.252.70.140 True
09: 162.252.70.133

13: 109.105.98.187 False
14: 84.116.130.241 False
15: 84.116.136.142 True

01: 128.9.112.7 False
02: 198.32.16.30 False
03: 137.164.23.225 False
04: 137.164.11.27 False
05: 64.57.20.82 False
06: 162.252.70.115 True
07: 162.252.70.144 True
08: 162.252.70.140 True
09: 64.57.29.225 False
11: 109.105.97.144 True
12: 109.105.98.186 False
13: 109.105.98.187 False
14: 84.116.130.241 False
15: 84.116.130.26 True
16: 84.116.228.82 True
17: 84.116.228.34 True
18: 84.116.228.218 False

01: 128.9.112.7 False
02: 198.32.16.30 False
03: 137.164.27.241 False
04: 137.164.26.201 False
05: 162.252.70.115 True
06: 162.252.70.144 True
07: 162.252.70.140 True
08: 162.252.70.60 True
09: 162.252.70.136 False
10: 62.40.124.44 False
11: 62.40.98.81 False
12: 62.40.98.128 False
13: 62.40.98.131 False
14: 62.40.125.246 False
15: 212.191.224.82 False
16: 212.182.56.197 False
17: 87.246.210.73 False

01: 128.9.112.7 False
02: 198.32.16.30 False
03: 137.164.27.241 False
04: 137.164.26.201 False
05: 162.252.70.115 T

01: 128.9.112.7 False
02: 198.32.16.30 False
03: 137.164.23.225 False
04: 137.164.11.7 False
05: 64.57.20.82 False
06: 162.252.70.115 True
07: 162.252.70.144 True
08: 162.252.70.140 True
09: 162.252.69.182 False
10: 162.252.69.183 False
12: 50.56.6.255 False
13: 50.56.6.129 False
14: 50.56.6.57 False

01: 128.9.112.7 False
02: 198.32.16.30 False
03: 137.164.27.241 False
04: 137.164.26.201 False
05: 162.252.70.115 True
06: 162.252.70.144 True
07: 162.252.70.140 True
08: 162.252.70.60 True
09: 162.252.70.136 False
10: 62.40.124.44 False
11: 62.40.98.79 False
12: 62.40.98.77 False
13: 62.40.124.70 False
14: 193.51.177.116 True
15: 193.51.181.101 False

01: 128.9.112.7 False
02: 198.32.16.30 False
03: 137.164.23.225 False
04: 137.164.11.35 False
05: 64.57.20.82 False
06: 162.252.70.115 True
07: 162.252.70.144 True
08: 162.252.70.140 True
09: 64.57.29.225 False
11: 109.105.97.134 True
12: 109.105.97.140 True
13: 109.105.97.126 True
14: 109.105.97.9 True
15: 109.105.98.65 False

01: 128.9.11

...

09: 162.252.70.136 False
10: 62.40.124.44 False
11: 62.40.98.81 False
12: 62.40.98.128 False
13: 62.40.98.97 False
14: 62.40.98.17 False
15: 62.40.124.6 False
16: 88.200.7.241 False
17: 88.200.7.236 False
18: 88.200.2.3 False
19: 178.172.82.139 False

01: 128.9.112.7 False
02: 198.32.16.30 False
03: 137.164.27.241 False
04: 137.164.26.201 False
05: 162.252.70.115 True
06: 162.252.70.144 True
07: 162.252.70.140 True
08: 162.252.70.60 True
09: 162.252.70.136 False
10: 62.40.124.44 False
11: 62.40.98.79 False
12: 62.40.98.77 False
13: 62.40.98.153 False
14: 62.40.124.62 False
15: 193.51.177.73 False

01: 128.9.112.7 False
02: 198.32.16.30 False
03: 137.164.23.225 False
04: 137.164.11.37 False
05: 64.57.20.82 False
06: 162.252.70.115 True
07: 162.252.70.144 True
08: 162.252.70.140 True
09: 64.57.29.225 False
11: 109.105.97.144 True
12: 80.249.209.203 False
13: 80.249.209.192 False
14: 146.172.105.10 True
15: 146.172.100.37 True
16: 146.172.101.225 True
17: 146.172.99.206 False
18: 193.212.

02: 198.32.16.30 False
03: 137.164.27.241 False
04: 137.164.26.201 False
05: 162.252.70.115 True
06: 162.252.70.144 True
07: 162.252.70.140 True
08: 162.252.70.60 True
09: 162.252.70.136 False
10: 62.40.124.44 False
11: 62.40.98.81 False
12: 62.40.98.128 False
13: 62.40.98.131 False
14: 62.40.125.246 False
15: 212.191.224.74 False
16: 148.81.166.125 False
17: 148.81.175.54 False

01: 128.9.112.7 False
02: 198.32.16.30 False
03: 137.164.27.241 False
04: 137.164.26.201 False
05: 162.252.70.115 True
06: 162.252.70.144 True
07: 162.252.70.140 True
08: 162.252.70.60 True
09: 162.252.70.136 False
10: 62.40.124.44 False
11: 62.40.98.81 False
12: 62.40.98.128 False
13: 62.40.124.218 False
14: 188.1.145.230 False
15: 188.1.37.90 False
16: 129.187.0.150 True
17: 129.187.0.186 True
18: 129.187.0.172 False

01: 128.9.112.7 False
02: 198.32.16.30 False
03: 137.164.27.241 False
04: 137.164.26.201 False
05: 162.252.70.115 True
06: 162.252.70.144 True
07: 162.252.70.140 True
08: 162.252.70.60 True
09:

10: 206.223.119.6 False
11: 216.113.123.173 False
12: 216.113.126.177 False
13: 216.113.126.177 False
14: 216.113.57.46 False

01: 128.9.112.7 False
02: 198.32.16.30 False
03: 137.164.27.241 False
04: 137.164.26.201 False
05: 162.252.70.115 True
06: 162.252.70.144 True
07: 162.252.70.140 True
08: 162.252.70.60 True
09: 162.252.70.136 False
10: 62.40.124.44 False
11: 62.40.98.81 False
12: 62.40.98.128 False

01: 128.9.112.7 False
02: 198.32.16.30 False
03: 137.164.27.241 False
04: 137.164.26.201 False
05: 162.252.70.115 True
06: 162.252.70.144 True
07: 162.252.70.140 True
08: 162.252.70.60 True
09: 162.252.70.136 False
10: 62.40.124.44 False
11: 62.40.98.79 False
12: 62.40.98.77 False
13: 62.40.124.70 False
14: 193.51.177.235 True
15: 193.51.177.35 False
16: 193.51.189.79 False

01: 128.9.112.7 False
02: 198.32.16.30 False
03: 137.164.27.241 False
04: 137.164.26.201 False
05: 162.252.70.115 True
06: 162.252.70.144 True
07: 162.252.70.140 True
08: 162.252.70.60 True
09: 162.252.70.136 Fa

02: 198.32.16.30 False
03: 137.164.27.241 False
04: 137.164.26.201 False
05: 162.252.70.115 True
06: 162.252.70.144 True
07: 162.252.70.140 True
08: 162.252.70.133 True
09: 162.252.70.130 True
10: 162.252.70.92 False
11: 192.5.89.253 False
12: 192.5.89.53 False

01: 128.9.112.7 False
02: 198.32.16.30 False
03: 137.164.27.241 False
04: 137.164.26.201 False
05: 162.252.70.115 True
06: 162.252.70.144 True
07: 162.252.70.140 True
08: 162.252.70.60 True
09: 162.252.70.136 True
10: 162.252.70.139 False
11: 196.32.209.237 False
12: 196.32.210.177 True
13: 196.32.209.80 False
14: 196.32.209.222 False
15: 155.232.1.14 True
16: 155.232.64.69 False
17: 155.232.27.86 False

01: 128.9.112.7 False
02: 198.32.16.30 False
03: 137.164.23.225 False
04: 137.164.11.35 False
05: 64.57.20.82 False
06: 162.252.70.115 True
07: 162.252.70.144 True
08: 162.252.70.140 True
09: 162.252.70.133 True
10: 162.252.70.130 True
11: 206.126.236.45 False
12: 206.126.236.140 False
13: 166.49.208.76 False
14: 213.137.183.33

31

In [77]:
vpns = sum(1 for v in bins.values() if v)
print('{:,d} ({:.2%})'.format(vpns, vpns / len(bins)))

11 (35.48%)


In [81]:
bins

defaultdict(bool,
            {'162.252.70.115': True,
             '162.252.70.144': False,
             '162.252.70.140': True,
             '162.252.70.60': False,
             '162.252.70.25': False,
             '162.252.70.23': False,
             '162.252.70.20': False,
             '162.252.70.15': True,
             '162.252.70.133': False,
             '162.252.70.130': True,
             '162.252.70.17': True,
             '162.252.70.70': True,
             '162.252.70.84': True,
             '162.252.70.45': True,
             '162.252.70.136': True,
             '162.252.70.38': True,
             '162.252.70.46': False,
             '162.252.70.153': False,
             '162.252.70.86': False,
             '162.252.70.121': False,
             '162.252.70.137': True,
             '162.252.70.146': False,
             '162.252.70.139': False,
             '162.252.70.110': False,
             '198.71.45.61': False,
             '162.252.70.142': False,
             '162.2

In [82]:
test['162.252.70.144']

{('162.252.70.109', '146.57.255.240'),
 ('162.252.70.140', '128.135.247.126'),
 ('162.252.70.140', '141.225.250.25'),
 ('162.252.70.140', '144.92.254.228'),
 ('162.252.70.140', '149.165.254.185'),
 ('162.252.70.140', '162.252.69.178'),
 ('162.252.70.140', '162.252.69.182'),
 ('162.252.70.140', '162.252.70.117'),
 ('162.252.70.140', '162.252.70.133'),
 ('162.252.70.140', '162.252.70.153'),
 ('162.252.70.140', '162.252.70.60'),
 ('162.252.70.140', '192.122.183.45'),
 ('162.252.70.140', '192.5.143.28'),
 ('162.252.70.140', '198.49.182.4'),
 ('162.252.70.140', '198.71.45.157'),
 ('162.252.70.140', '198.71.45.232'),
 ('162.252.70.140', '198.71.45.61'),
 ('162.252.70.140', '198.71.46.183'),
 ('162.252.70.140', '205.213.119.9'),
 ('162.252.70.140', '206.223.119.116'),
 ('162.252.70.140', '64.57.20.0'),
 ('162.252.70.140', '64.57.28.105'),
 ('162.252.70.140', '64.57.28.2'),
 ('162.252.70.140', '64.57.29.225'),
 ('162.252.70.142', '162.252.70.135'),
 ('162.252.70.35', '198.71.46.45'),
 ('162.25